importiamo le librerie necessarie.
useremo anche la libreria peakutils

In [ ]:
import numpy as np
import peakutils as pk
import matplotlib.pyplot as plt


Leggiamo i dati dal file CO.csv, invertiamo l'ordine dei dati e sezioniamo un intervallo di numeri d'onda corrispondente alla transizione 0->1.


In [ ]:
spettro = np.genfromtxt('CO.csv', delimiter=',',skip_header=1,names=True)

sp_x=spettro['cm1'][::-1] # invertiamo l'ordine del vettore con la notazione [::-1]
sp_y=spettro['A'][::-1]

plt.plot(sp_x,sp_y)
plt.show()


In [ ]:
banda_01=(sp_x < 2250) & (sp_x > 2050)

x_01=sp_x[banda_01]
y_01=sp_y[banda_01]

plt.plot(x_01,y_01)
plt.show()

Andiamo a selezionare una regione interessante dello spettro, in questo caso la banda per la transizione vibrazionale 0→1

Passiamo all'analisi dello spettro. Troviamo i picchi sfruttando le capacità in peakutils.indexes

In [ ]:
dx=sp_x[1]-sp_x[0]
print('risoluzione = %.2f cm^-1'%(dx))
ind=pk.indexes(y_01, thres=0.1, min_dist=2/dx)
px=x_01[ind]; py=y_01[ind]

plt.plot(x_01,y_01)
plt.plot(px, py, 'ob')
plt.show()


indexes è più adatta di signal.find_peaks_cwt per l'analisi degli spettri: in particolare permette di regolare la soglia thres per l'altezza e la distanza minima tra i picchi; questa è misurata sull'indice, non sulle unità dell'ascissa che infatti non viene passata a indexes. In questo caso abbiamo chiesto una separazione minima fra i picchi di 2 cm^-1.

Adesso andiamo a numerare i picchi, tramite l'indice m=J+1 per le transizioni J→J+1, e m=-J per le transizioni J→J-1. Cominciamo con il creare un indice m fittizio, per aggiustarlo successivamente. 

In [ ]:
m = np.arange(len(ind))

plt.plot(m, px, 'o-r')
plt.show()


Ora bisogna aggiustare l'indice m. Possiamo farlo sistematicamente approfittando della discontinuità intorno ad m=0, visibile anche nel grafico. Intorno ad m=0 la distanza tra i picchi è doppia.


In [ ]:
int_medio=(px[-1]-px[0])/len(px)
intervalli=px[1:]-px[0:-1]
pos= np.argmax(intervalli>int_medio*1.6)
print('int_medio =', int_medio)
print('pos trovata = ', pos)



Adesso int_medio è la distanza media tra i picchi e pos contiene la posizione della prima e unica ricorrenza di una distanza tra i picchi maggiore di 1.6 volte la distanza media. 

In [ ]:
m[pos+1:]-=pos
m[:pos+1]-= pos+1
plt.plot(m ,px, 'o-r')
plt.show()
m


Infine andiamo ad effettuare un fit polinomiale delle posizioni dei picchi in funzione di m. Il polinomio, che tiene conto della distorsione centrifuga e dell'accoppiamento rotovibrazionale, è di terzo grado. La libreria numpy consente questo calcolo tramite la funzione polyfit. 

In [ ]:
coeff = np.polyfit(m, px, 3)
polinomio=np.poly1d(coeff)
valori_fit=polinomio(m)
print(polinomio)

polyfit ritorna i coefficienti del polinomio. Usate il riquadro sopra per visionarli. Per calcolare i valori del polinomio è conveniente usare la funzione poly1d che permette di trasformare i coefficienti in un oggetto che può essere chiamato come una funzione. Provate per esempio a chiamare polinomio(x) con diversi valori di x.  

Verifichiamo il nostro fit. La grafica è la migliore prima opzione.

In [ ]:
plt.plot(m, px,'o-r')
plt.plot(m,valori_fit,'+b')
plt.show()

